In [7]:
import numpy as np
import matplotlib.pyplot as plt
import wave
import scipy
from IPython.display import Audio

In [8]:
# Load audio file into a signal
def load_audio(filename):
    file = wave.open(filename)
    nframes = file.getnframes()
    # create numpy array of sampled points in audio
    signal = np.frombuffer(file.readframes(nframes), dtype=np.int16)
    signal = signal.astype(float) # best for numerical processing
    framerate = file.getframerate()
    return signal, framerate

# Constructs and plays audio from a signal
def play_audio(signal, framerate):
    return Audio(data=signal, rate=framerate)

x, fs = load_audio('scales.wav')
fs*=2 #for scales.wav recording idk why
print(fs)
play_audio(x, fs)

44100


In [9]:
# take STFT and plot spectrogram
f,t,X_complex = scipy.signal.stft(x, fs=fs, window='hann', nperseg=4096, noverlap=3072)
X_complex[:5,:]=0 # remove low frequencies and DC from signal
X_complex[400:,:]=0 #remove aliasing
X=np.abs(X_complex) # only care about mag
plt.imshow(X, norm='symlog', origin='lower', extent=(t[0],t[-1],f[0],f[-1]), aspect='auto')
plt.show()

AttributeError: module 'scipy' has no attribute 'signal'

In [ ]:
# run harmonic product spectrum algorithm on stft
N=5
hps=np.ones( (int(np.ceil(X.shape[0]/N)), X.shape[1]) )
for n in range(N):
    X_n = X[::(n+1),:]
    hps *= X_n[:hps.shape[0],:]
    
plt.imshow(hps, norm='symlog', origin='lower', extent=(t[0],t[-1],f[0],f[-1]/N), aspect='auto')
plt.show()

In [ ]:
f_hps=f[::N]/N
hps_peaks = np.zeros(hps.shape[1])
hero = np.zeros(hps.shape)
global_max_peak = np.max(hps)
for m in range(hps.shape[1]):
    max_peak = np.max(hps[:,m])
    peak = np.argmax(hps[:,m])
    #if max_peak > global_max_peak/1e9:
    hps_peaks[m] = f_hps[peak]
    hero[peak,m] = 1

plt.imshow(hero, norm='symlog', origin='lower', extent=(t[0],t[-1],f[0],f[-1]/N), aspect='auto')
plt.show()

hps_peaks=scipy.signal.medfilt(hps_peaks, [21])

In [ ]:
# generate table of note frequencies
# start with a scale from A4 up an octave
A4_FREQ = 440 # Hz
base_scale=['A4','A#4','B4','C4','C#4','D4','D#4','E4','F4','F#4','G4','G#4']
base_notes = {base_scale[n]: A4_FREQ * 2**(n/12) for n in range(len(base_scale))}
# other octaves will differ in freq. by powers of 2
note_table=dict()
for octave in range(2,8):
    scale=[note[:-1]+str(octave) for note in base_scale]
    for note in scale:
        note_table[note] = base_notes[note[:-1]+'4'] * 2**(octave-4)
print(note_table)

In [ ]:
def nearest_note(f):
    if f == 0:
        return None
    
    delta=np.inf
    est_note=None
    for note in note_table:
        if np.abs(note_table[note] - f) < delta:
            delta = np.abs(note_table[note] - f)
            est_note = note
            
    return est_note

melody = [nearest_note(f) for f in hps_peaks]
#print(melody)
melody_freq = [None if note is None else note_table[note] for note in melody]
y,xmin,xmax=[],[],[]
for m in range(len(melody_freq)):
    if melody_freq[m] is not None:
        y.append(melody_freq[m])
        xmin.append(m)
        xmax.append(m+1)

#print(melody_freq)
plt.hlines(y,xmin,xmax)
#plt.imshow(hps, norm='symlog', origin='lower', extent=(t[0],t[-1],f[0],f[-1]/N), aspect='auto')
plt.show()

In [ ]:
from scipy.io import wavfile

knock_rate, knock = wavfile.read("knock.wav")
fft = np.fft.rfft(knock)
fs = np.fft.rfftfreq(knock.size, d=1 / knock_rate)
nominal_freq = fs[np.argmax(fft)]
nominal_freq

In [ ]:
import librosa
from IPython.display import Audio

base, fs = librosa.load("knock.wav")
song = np.zeros(int((xmax[-1]- xmin[0]) * fs))
prev = 0
for i, y_val in enumerate(y):
    this_note = librosa.effects.pitch_shift(base, sr=fs, n_steps=12 * np.log2(y_val / nominal_freq))
    this_note = librosa.effects.time_stretch(this_note, rate=this_note.size / (fs * (xmax[i]-xmin[i])))
    song[prev:this_note.size+prev] = this_note
    prev += this_note.size


Audio(data=song, rate=fs)